# 🚗 **Section 1: Loading Data and Initial Preprocessing for Parking Lot Analysis**

## 📥 Step 1: Import Required Libraries & Load the Dataset

In [1]:
import numpy as np
import pandas as pd
from datetime import datetime
import matplotlib.pyplot as plt

# Load the dataset into a DataFrame
data = pd.read_csv('dataset.csv')

In [2]:
# Load the dataset into a DataFrame
data = pd.read_csv('dataset.csv')

# Combine date and time columns to create a full timestamp
data['Timestamp'] = pd.to_datetime(
    data['LastUpdatedDate'] + ' ' + data['LastUpdatedTime'],
    dayfirst=True
)

In [3]:
# Combine date and time columns to create a single datetime column
data['DateTime'] = pd.to_datetime(
    data['LastUpdatedDate'] + ' ' + data['LastUpdatedTime'],
    dayfirst=True
)

# Display the first few records to inspect the data structure
data.head()

ID SystemCodeNumber  Capacity   Latitude  Longitude  Occupancy VehicleType  \
0   0      BHMBCCMKT01       577  26.144536  91.736172         61         car   
1   1      BHMBCCMKT01       577  26.144536  91.736172         64         car   
2   2      BHMBCCMKT01       577  26.144536  91.736172         80         car   
3   3      BHMBCCMKT01       577  26.144536  91.736172        107         car   
4   4      BHMBCCMKT01       577  26.144536  91.736172        150        bike   

  TrafficConditionNearby  QueueLength  IsSpecialDay LastUpdatedDate  \
0                    low            1             0      04-10-2016   
1                    low            1             0      04-10-2016   
2                    low            2             0      04-10-2016   
3                    low            2             0      04-10-2016   
4                    low            2             0      04-10-2016   

  LastUpdatedTime           Timestamp            DateTime  
0        07:59:00 2016-10-04 07:59:00 2016-10-04 07:59:00  
1        08:25:00 2016-10-04 08:25:00 2016-10-04 08:25:00  
2        08:59:00 2016-10-04 08:59:00 2016-10-04 08:59:00  
3        09:32:00 2016-10-04 09:32:00 2016-10-04 09:32:00  
4        09:59:00 2016-10-04 09:59:00 2016-10-04 09:59:00

In [4]:
# Map traffic condition to numeric codes: low=0, average=1, high=2
traffic_map = {'low': 0, 'average': 1, 'high': 2}
data['TrafficLevel'] = data['TrafficConditionNearby'].map(traffic_map)

# Assign weights to vehicle types for modeling
vehicle_weight_map = {
    'cycle': 0.3,
    'bike': 0.5,
    'car': 1.0,  # baseline
    'truck': 1.5
}
data['VehicleWeight'] = data['VehicleType'].map(vehicle_weight_map)
data['VehicleWeight'] = data['VehicleWeight'].fillna(1.0)  # Default to 'car'

# Display the first few rows to inspect the data structure
data.head()

ID SystemCodeNumber  Capacity   Latitude  Longitude  Occupancy VehicleType  \
0   0      BHMBCCMKT01       577  26.144536  91.736172         61         car   
1   1      BHMBCCMKT01       577  26.144536  91.736172         64         car   
2   2      BHMBCCMKT01       577  26.144536  91.736172         80         car   
3   3      BHMBCCMKT01       577  26.144536  91.736172        107         car   
4   4      BHMBCCMKT01       577  26.144536  91.736172        150        bike   

  TrafficConditionNearby  QueueLength  IsSpecialDay LastUpdatedDate  \
0                    low            1             0      04-10-2016   
1                    low            1             0      04-10-2016   
2                    low            2             0      04-10-2016   
3                    low            2             0      04-10-2016   
4                    low            2             0      04-10-2016   

  LastUpdatedTime           Timestamp            DateTime  TrafficLevel  \
0        07:59:00 2016-10-04 07:59:00 2016-10-04 07:59:00             0   
1        08:25:00 2016-10-04 08:25:00 2016-10-04 08:25:00             0   
2        08:59:00 2016-10-04 08:59:00 2016-10-04 08:59:00             0   
3        09:32:00 2016-10-04 09:32:00 2016-10-04 09:32:00             0   
4        09:59:00 2016-10-04 09:59:00 2016-10-04 09:59:00             0   

   VehicleWeight  
0            1.0  
1            1.0  
2            1.0  
3            1.0  
4            0.5

# 🧼 **Step 2: Data Cleaning and Feature Engineering**

Data Preprocessing involves the following steps:
1. Transforming categorical variables like **traffic** and **vehicle type** into numerical format.
2. Generating normalized versions of:
   * **Occupancy** (represented as a fraction of total capacity)
   * **Queue length** (scaled to fall between 0 and 1)

## **2A. Transform Categorical Data**

In [5]:
# Map 'TrafficConditionNearby' to numeric values: low=0, average=1, high=2

traffic_map = {'low': 0, 'average': 1, 'high': 2}
data['TrafficLevel'] = data['TrafficConditionNearby'].map(traffic_map)

In [6]:
# Assign relative weights to each vehicle type
vehicle_map = {
    'cycle': 0.3,
    'bike': 0.5,
    'car': 1.0,   # baseline
    'truck': 1.5
}
data['VehicleWeight'] = data['VehicleType'].map(vehicle_map)

In [7]:
# Fill missing values with defaults for traffic and vehicle type

data['TrafficLevel'] = data['TrafficLevel'].fillna(1)      # Default to 'average'
data['VehicleWeight'] = data['VehicleWeight'].fillna(1.0)  # Default to 'car'

## **2B. Feature Scaling and Normalization**

In [8]:
# Calculate occupancy as a proportion of total spots

data['OccupancyRate'] = data['Occupancy'] / data['Capacity']

In [9]:
# Scale queue length to a 0-1 range

max_queue = data['QueueLength'].max()
data['QueueNorm'] = data['QueueLength'] / max_queue

## **2C. Assemble Final Feature Set for Model Input**

In [10]:
# This step ensures that our model only uses relevant and clean columns.

# Select relevant columns for modeling
final_features = data[['SystemCodeNumber', 'Timestamp', 'OccupancyRate', 'QueueNorm',
                      'TrafficLevel', 'IsSpecialDay', 'VehicleWeight']]

In [11]:
# Show a preview of the processed features
final_features.head()

SystemCodeNumber           Timestamp  OccupancyRate  QueueNorm  \
0      BHMBCCMKT01 2016-10-04 07:59:00       0.105719   0.066667   
1      BHMBCCMKT01 2016-10-04 08:25:00       0.110919   0.066667   
2      BHMBCCMKT01 2016-10-04 08:59:00       0.138648   0.133333   
3      BHMBCCMKT01 2016-10-04 09:32:00       0.185442   0.133333   
4      BHMBCCMKT01 2016-10-04 09:59:00       0.259965   0.133333   

   TrafficLevel  IsSpecialDay  VehicleWeight  
0             0             0            1.0  
1             0             0            1.0  
2             0             0            1.0  
3             0             0            1.0  
4             0             0            0.5

# Step 3: Model 1 – Simple Linear Pricing Approach

This baseline model adjusts parking prices in real time based on how full the lot is.  
The price at each time step is determined by the previous price and the current occupancy ratio.

A straightforward approach: as occupancy rises, so does the price, in a linear fashion.

**Formula Example:**
Price<sub>t+1</sub> = Price<sub>t</sub> + α × (Current Occupancy / Capacity)

In [12]:
# Set initial price and alpha parameter
start_price = 10
alpha_param = 5  # determines how much price reacts to occupancy

In [13]:
# Sort the DataFrame by lot and timestamp for sequential processing
data = data.sort_values(by=['SystemCodeNumber', 'Timestamp'])

In [14]:
# Add a price column, starting with the base price

data['Price'] = start_price
data['Price'] = data['Price'].astype(float)

In [15]:
# Recalculate occupancy rate for accuracy

data['OccupancyRate'] = data['Occupancy'] / data['Capacity']

In [16]:
# Loop through each parking lot to update prices over time
for lot_id in data['SystemCodeNumber'].unique():
    lot_df = data[data['SystemCodeNumber'] == lot_id].copy()

In [17]:
# Sequentially update price for each time entry in the lot
for idx in range(1, len(lot_df)):
    previous_price = lot_df.iloc[idx-1]['Price']
    occ_rate = lot_df.iloc[idx]['OccupancyRate']

In [18]:
# Compute the next price using a linear rule
updated_price = previous_price + alpha_param * occ_rate

In [19]:
# Keep the price within reasonable bounds
updated_price = max(5, min(updated_price, 30))

In [20]:
# Store the new price in the DataFrame
data.loc[lot_df.index[idx], 'Price'] = updated_price

In [21]:
# Display the first 20 rows with updated prices
data[['SystemCodeNumber', 'Timestamp', 'Occupancy', 'Capacity', 'Price']].head(20)

SystemCodeNumber           Timestamp  Occupancy  Capacity  Price
0       BHMBCCMKT01 2016-10-04 07:59:00         61       577   10.0
1       BHMBCCMKT01 2016-10-04 08:25:00         64       577   10.0
2       BHMBCCMKT01 2016-10-04 08:59:00         80       577   10.0
3       BHMBCCMKT01 2016-10-04 09:32:00        107       577   10.0
4       BHMBCCMKT01 2016-10-04 09:59:00        150       577   10.0
5       BHMBCCMKT01 2016-10-04 10:26:00        177       577   10.0
6       BHMBCCMKT01 2016-10-04 10:59:00        219       577   10.0
7       BHMBCCMKT01 2016-10-04 11:25:00        247       577   10.0
8       BHMBCCMKT01 2016-10-04 11:59:00        259       577   10.0
9       BHMBCCMKT01 2016-10-04 12:29:00        266       577   10.0
10      BHMBCCMKT01 2016-10-04 13:02:00        269       577   10.0
11      BHMBCCMKT01 2016-10-04 13:29:00        263       577   10.0
12      BHMBCCMKT01 2016-10-04 14:02:00        238       577   10.0
13      BHMBCCMKT01 2016-10-04 14:29:00        215       577   10.0
14      BHMBCCMKT01 2016-10-04 14:57:00        192       577   10.0
15      BHMBCCMKT01 2016-10-04 15:30:00        165       577   10.0
16      BHMBCCMKT01 2016-10-04 16:04:00        162       577   10.0
17      BHMBCCMKT01 2016-10-04 16:31:00        143       577   10.0
18      BHMBCCMKT01 2016-10-05 07:57:00         54       577   10.0
19      BHMBCCMKT01 2016-10-05 08:30:00         59       577   10.0

# Step 4: Model 2 – Demand-Driven Price Adjustment

In [22]:
# Set base price and demand sensitivity
base_amt = 10
lambda_factor = 0.8  # Controls demand impact on price

In [23]:
# Map traffic conditions to numeric for demand calculation
traffic_map2 = {'low': 0.5, 'average': 1.0, 'high': 1.5}
data['TrafficLevel'] = data['TrafficConditionNearby'].map(traffic_map2).fillna(1.0)

In [24]:
# Assign numeric weights to vehicle types for demand
vehicle_weight_map2 = {'car': 1.0, 'bike': 0.7, 'truck': 1.2, 'cycle': 0.5}
data['VehicleWeight'] = data['VehicleType'].map(vehicle_weight_map2).fillna(1.0)

In [25]:
# Normalize queue length for demand calculation
max_queue2 = data['QueueLength'].max()
data['QueueNorm'] = data['QueueLength'] / max_queue2

In [26]:
# Ensure occupancy rate is up to date for demand model
data['OccupancyRate'] = data['Occupancy'] / data['Capacity']

In [27]:
# Set weights for each demand factor
alpha_w = 3.0    # occupancy
beta_w = 2.0     # queue
gamma_w = 1.5    # traffic (subtracted)
delta_w = 4.0    # special day
epsilon_w = 1.0  # vehicle type

In [28]:
# Compute demand score for each row
data['DemandScore'] = (alpha_w * data['OccupancyRate'] +
                      beta_w * data['QueueNorm'] -
                      gamma_w * data['TrafficLevel'] +
                      delta_w * data['IsSpecialDay'] +
                      epsilon_w * data['VehicleWeight'])

# Normalize demand to 0-1 for price scaling
demand_min = data['DemandScore'].min()
demand_max = data['DemandScore'].max()
data['DemandNorm'] = (data['DemandScore'] - demand_min) / (demand_max - demand_min)

# Initialize price column for demand model
data['Price'] = base_amt
data['Price'] = data['Price'].astype(float)

# Update prices for each lot based on demand
for lot_id in data['SystemCodeNumber'].unique():
    lot_df = data[data['SystemCodeNumber'] == lot_id].copy()
    for idx in range(len(lot_df)):
        demand_val = lot_df.iloc[idx]['DemandNorm']
        new_price = base_amt * (1 + lambda_factor * demand_val)
        new_price = max(base_amt * 0.5, min(new_price, base_amt * 2.0))
        data.loc[lot_df.index[idx], 'Price'] = new_price

# Show first 20 rows with demand-based prices
data[['SystemCodeNumber', 'Timestamp', 'Occupancy', 'QueueLength', 'TrafficConditionNearby',
      'IsSpecialDay', 'VehicleType', 'Price']].head(20)


SystemCodeNumber           Timestamp  Occupancy  QueueLength  \
0       BHMBCCMKT01 2016-10-04 07:59:00         61            1   
1       BHMBCCMKT01 2016-10-04 08:25:00         64            1   
2       BHMBCCMKT01 2016-10-04 08:59:00         80            2   
3       BHMBCCMKT01 2016-10-04 09:32:00        107            2   
4       BHMBCCMKT01 2016-10-04 09:59:00        150            2   
5       BHMBCCMKT01 2016-10-04 10:26:00        177            3   
6       BHMBCCMKT01 2016-10-04 10:59:00        219            6   
7       BHMBCCMKT01 2016-10-04 11:25:00        247            5   
8       BHMBCCMKT01 2016-10-04 11:59:00        259            5   
9       BHMBCCMKT01 2016-10-04 12:29:00        266            8   
10      BHMBCCMKT01 2016-10-04 13:02:00        269            7   
11      BHMBCCMKT01 2016-10-04 13:29:00        263            7   
12      BHMBCCMKT01 2016-10-04 14:02:00        238            5   
13      BHMBCCMKT01 2016-10-04 14:29:00        215            3   
14      BHMBCCMKT01 2016-10-04 14:57:00        192            3   
15      BHMBCCMKT01 2016-10-04 15:30:00        165            2   
16      BHMBCCMKT01 2016-10-04 16:04:00        162            1   
17      BHMBCCMKT01 2016-10-04 16:31:00        143            2   
18      BHMBCCMKT01 2016-10-05 07:57:00         54            1   
19      BHMBCCMKT01 2016-10-05 08:30:00         59            1   

   TrafficConditionNearby  IsSpecialDay VehicleType      Price  
0                     low             0         car  11.219162  
1                     low             0         car  11.233854  
2                     low             0         car  11.437796  
3                     low             0         car  11.570020  
4                     low             0        bike  11.498031  
5                     low             0         car  12.038412  
6                    high             0       truck  11.396387  
7                 average             0         car  11.925966  
8                 average             0       cycle  11.513784  
9                    high             0        bike  11.406780  
10                   high             0         car  11.578455  
11                   high             0         car  11.549071  
12                   high             0         car  11.175468  
13                average             0       truck  11.706462  
14                average             0        bike  11.122877  
15                    low             0         car  11.854059  
16                    low             0        bike  11.431212  
17                average             0         car  11.039897  
18                    low             0         car  11.184882  
19                average             0         car  10.502944

# Step 5: Model 3 – Pricing with Competitor Awareness and Smart Rerouting

### Objectives:
* Use location data to identify nearby parking competitors
* Adjust prices based on local competition
* Suggest rerouting if a lot is full and cheaper options are close

### Key Points:
* Calculate distances using latitude/longitude
* Find competitors within a set distance (e.g., 1 km)
* Adjust prices up or down based on nearby lots
* Suggest rerouting if full and cheaper lots are available
* Raise price if competitors are more expensive

In [29]:
# Function to compute distance (km) between two lat/lon points using Haversine formula
def haversine_distance(lat1, lon1, lat2, lon2):
    R = 6371  # Earth radius in kilometers
    phi1, phi2 = np.radians(lat1), np.radians(lat2)
    d_phi = np.radians(lat2 - lat1)
    d_lambda = np.radians(lon2 - lon1)

    a = np.sin(d_phi/2)**2 + np.cos(phi1)*np.cos(phi2)*np.sin(d_lambda/2)**2
    c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1 - a))
    return R * c

In [30]:
# Set distance threshold for competitor search (e.g., 1 km)
comp_radius = 1.0

In [31]:
# Store the most recent price for each lot for quick access
latest_price_lookup = data.groupby('SystemCodeNumber')['Price'].last()

In [32]:
# Find competitor lots within a certain radius
def get_nearby_competitors(current_lot):
    lat1 = data.loc[data['SystemCodeNumber'] == current_lot, 'Latitude'].iloc[0]
    lon1 = data.loc[data['SystemCodeNumber'] == current_lot, 'Longitude'].iloc[0]
    
    close_lots = []
    for lot in data['SystemCodeNumber'].unique():
        if lot == current_lot:
            continue
        lat2 = data.loc[data['SystemCodeNumber'] == lot, 'Latitude'].iloc[0]
        lon2 = data.loc[data['SystemCodeNumber'] == lot, 'Longitude'].iloc[0]
        dist = haversine_distance(lat1, lon1, lat2, lon2)
        if dist <= comp_radius:
            close_lots.append(lot)
    return close_lots

In [33]:
# Adjust prices based on competitor proximity and occupancy
for lot in data['SystemCodeNumber'].unique():
    lot_indices = data[data['SystemCodeNumber'] == lot].index
    
    close_lots = get_nearby_competitors(lot)
    close_prices = latest_price_lookup.loc[close_lots] if close_lots else pd.Series(dtype=float)
    
    for idx in lot_indices:
        curr_price = data.loc[idx, 'Price']
        occ = data.loc[idx, 'Occupancy']
        cap = data.loc[idx, 'Capacity']
        
        # If lot is nearly full, check competitors
        if occ >= 0.9 * cap and not close_prices.empty:
            min_comp_price = close_prices.min()
            if min_comp_price < curr_price:
                # Lower price or suggest reroute
                new_price = max(5, min_comp_price * 0.95)
                data.loc[idx, 'Price'] = new_price
                data.loc[idx, 'RerouteSuggestion'] = True
            else:
                # Raise price if competitors are pricier
                new_price = min(30, curr_price * 1.05)
                data.loc[idx, 'Price'] = new_price
                data.loc[idx, 'RerouteSuggestion'] = False
        else:
            data.loc[idx, 'RerouteSuggestion'] = False

In [34]:
# Preview first 20 rows with updated prices and reroute suggestions
data[['SystemCodeNumber', 'Timestamp', 'Occupancy', 'Capacity', 'Price', 'RerouteSuggestion']].head(20)

SystemCodeNumber           Timestamp  Occupancy  Capacity      Price  \
0       BHMBCCMKT01 2016-10-04 07:59:00         61       577  11.219162   
1       BHMBCCMKT01 2016-10-04 08:25:00         64       577  11.233854   
2       BHMBCCMKT01 2016-10-04 08:59:00         80       577  11.437796   
3       BHMBCCMKT01 2016-10-04 09:32:00        107       577  11.570020   
4       BHMBCCMKT01 2016-10-04 09:59:00        150       577  11.498031   
5       BHMBCCMKT01 2016-10-04 10:26:00        177       577  12.038412   
6       BHMBCCMKT01 2016-10-04 10:59:00        219       577  11.396387   
7       BHMBCCMKT01 2016-10-04 11:25:00        247       577  11.925966   
8       BHMBCCMKT01 2016-10-04 11:59:00        259       577  11.513784   
9       BHMBCCMKT01 2016-10-04 12:29:00        266       577  11.406780   
10      BHMBCCMKT01 2016-10-04 13:02:00        269       577  11.578455   
11      BHMBCCMKT01 2016-10-04 13:29:00        263       577  11.549071   
12      BHMBCCMKT01 2016-10-04 14:02:00        238       577  11.175468   
13      BHMBCCMKT01 2016-10-04 14:29:00        215       577  11.706462   
14      BHMBCCMKT01 2016-10-04 14:57:00        192       577  11.122877   
15      BHMBCCMKT01 2016-10-04 15:30:00        165       577  11.854059   
16      BHMBCCMKT01 2016-10-04 16:04:00        162       577  11.431212   
17      BHMBCCMKT01 2016-10-04 16:31:00        143       577  11.039897   
18      BHMBCCMKT01 2016-10-05 07:57:00         54       577  11.184882   
19      BHMBCCMKT01 2016-10-05 08:30:00         59       577  10.502944   

   RerouteSuggestion  
0              False  
1              False  
2              False  
3              False  
4              False  
5              False  
6              False  
7              False  
8              False  
9              False  
10             False  
11             False  
12             False  
13             False  
14             False  
15             False  
16             False  
17             False  
18             False  
19             False

* Compute distances between lots using coordinates
* Identify competitors within 1 km (or chosen radius)
* If a lot is almost full, compare competitor prices
* Lower price and suggest reroute if cheaper lots are close
* Raise price if competitors are more expensive
* Otherwise, keep price steady

# Step 6: Real-Time Simulation – Linear Pricing Example

In [35]:
import pathway
print(pathway.__file__)  # Show where pathway is installed

c:\Users\user\AppData\Local\Programs\Python\Python313\Lib\site-packages\pathway\__init__.py


This is not the real Pathway package.
Visit https://pathway.com/developers/ to get Pathway.
Already tried that? Visit https://pathway.com/troubleshooting/ to get help.
Note: your platform is Windows-10-10.0.18363-SP0, your Python is CPython 3.13.1.


In [36]:
BASE_PRICE = 10
ALPHA = 5  # Linear price sensitivity

# List to collect simulated rows
sim_rows = []

# Sort for simulation order
data = data.sort_values(['SystemCodeNumber', 'Timestamp']).reset_index(drop=True)

# Track current price for each lot
current_price = {lot: BASE_PRICE for lot in data['SystemCodeNumber'].unique()}

# Simulate streaming: process each row in order
for idx, row in data.iterrows():
    lot = row['SystemCodeNumber']
    occ_rate = row['Occupancy'] / row['Capacity']
    # Update price
    new_price = current_price[lot] + ALPHA * occ_rate
    new_price = max(5, min(new_price, 30))
    current_price[lot] = new_price
    # Add row with updated price
    row_dict = row.to_dict()
    row_dict['Price'] = new_price
    sim_rows.append(row_dict)

# Convert to DataFrame
sim_df = pd.DataFrame(sim_rows)

# Preview first 20 simulated results
sim_df[['SystemCodeNumber', 'Timestamp', 'Occupancy', 'Capacity', 'Price']].head(20)

SystemCodeNumber           Timestamp  Occupancy  Capacity      Price
0       BHMBCCMKT01 2016-10-04 07:59:00         61       577  10.528596
1       BHMBCCMKT01 2016-10-04 08:25:00         64       577  11.083189
2       BHMBCCMKT01 2016-10-04 08:59:00         80       577  11.776430
3       BHMBCCMKT01 2016-10-04 09:32:00        107       577  12.703640
4       BHMBCCMKT01 2016-10-04 09:59:00        150       577  14.003466
5       BHMBCCMKT01 2016-10-04 10:26:00        177       577  15.537262
6       BHMBCCMKT01 2016-10-04 10:59:00        219       577  17.435009
7       BHMBCCMKT01 2016-10-04 11:25:00        247       577  19.575390
8       BHMBCCMKT01 2016-10-04 11:59:00        259       577  21.819757
9       BHMBCCMKT01 2016-10-04 12:29:00        266       577  24.124783
10      BHMBCCMKT01 2016-10-04 13:02:00        269       577  26.455806
11      BHMBCCMKT01 2016-10-04 13:29:00        263       577  28.734835
12      BHMBCCMKT01 2016-10-04 14:02:00        238       577  30.000000
13      BHMBCCMKT01 2016-10-04 14:29:00        215       577  30.000000
14      BHMBCCMKT01 2016-10-04 14:57:00        192       577  30.000000
15      BHMBCCMKT01 2016-10-04 15:30:00        165       577  30.000000
16      BHMBCCMKT01 2016-10-04 16:04:00        162       577  30.000000
17      BHMBCCMKT01 2016-10-04 16:31:00        143       577  30.000000
18      BHMBCCMKT01 2016-10-05 07:57:00         54       577  30.000000
19      BHMBCCMKT01 2016-10-05 08:30:00         59       577  30.000000

## ✅ **Step 7: Interactive Visualization with Bokeh**

In [37]:
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import ColumnDataSource
from bokeh.palettes import Category10
from bokeh.layouts import layout

# The rest of your code goes here...

In [38]:
output_notebook()

# Use processed DataFrame from pricing steps
# Ensure Timestamp is datetime
data['Timestamp'] = pd.to_datetime(data['Timestamp'])

Loading BokehJS ...

In [39]:
# Build a Bokeh plot for price over time
p = figure(
    x_axis_type='datetime',
    title='Dynamic Parking Price Over Time',
    height=400,
    width=800
)

p.line(data['Timestamp'], data['Price'], line_width=2, color='crimson', legend_label='Price')

p.xaxis.axis_label = 'Time'
p.yaxis.axis_label = 'Price ($)'
p.legend.location = 'top_left'

show(p)

1. Multi-line plot: Visualize pricing for multiple parking lots in real time

In [40]:
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import ColumnDataSource, HoverTool
from bokeh.palettes import Viridis256
import pandas as pd

output_notebook()

data['Timestamp'] = pd.to_datetime(data['Timestamp'])

# Group by lot
lot_ids = data['SystemCodeNumber'].unique()

p = figure(
    x_axis_type='datetime',
    title='Pricing Over Time for Multiple Parking Lots',
    width=800,
    height=400
)
p.xaxis.axis_label = 'Time'
p.yaxis.axis_label = 'Price ($)'

palette = Viridis256
for i, lot in enumerate(lot_ids):
    lot_df = data[data['SystemCodeNumber'] == lot]
    source = ColumnDataSource(lot_df)
    color = palette[int(i * (255 / max(1, len(lot_ids)-1)))]
    p.line('Timestamp', 'Price', source=source, color=color, legend_label=f'Lot {lot}', line_width=2)
    p.scatter('Timestamp', 'Price', source=source, color=color, size=5, marker='circle')

p.legend.location = "top_left"
p.legend.click_policy = "hide"  

# Add hover tool
tooltips = [
    ('Lot', '@SystemCodeNumber'),
    ('Time', '@Timestamp{%F %T}'),
    ('Price', '@Price{$0.00}')
]
hover = HoverTool(tooltips=tooltips, formatters={'@Timestamp': 'datetime'}, mode='vline')
p.add_tools(hover)

show(p)

Loading BokehJS ...

2. Visualize your lot's prices versus competitors over time

In [41]:
competitor_rows = []

for lot in data['SystemCodeNumber'].unique():
    lot_df = data[data['SystemCodeNumber'] == lot]
    n = len(lot_df)
    comp_prices = np.random.uniform(8, 25, n)
    competitor_rows.append(
        pd.DataFrame({
            'SystemCodeNumber': lot,
            'Timestamp': lot_df['Timestamp'].values,
            'CompetitorPrice': comp_prices
        })
    )

df_competitor = pd.concat(competitor_rows, ignore_index=True)

In [42]:
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, HoverTool
from bokeh.palettes import Plasma256

# Use 'lot_ids', 'data', and 'df_competitor' as defined above

p = figure(
    x_axis_type='datetime',
    title='Your Price vs Competitor Price Over Time',
    width=800,
    height=400
)

palette = Plasma256

for i, lot in enumerate(lot_ids):
    lot_df = data[data['SystemCodeNumber'] == lot]
    comp_df = df_competitor[df_competitor['SystemCodeNumber'] == lot]
    source_yours = ColumnDataSource(lot_df)
    source_comp = ColumnDataSource(comp_df)
    color = palette[int(i * (255 / max(1, len(lot_ids)-1)))]
    p.line('Timestamp', 'Price', source=source_yours, color=color, legend_label=f'Your Lot {lot}', line_width=2)
    p.line('Timestamp', 'CompetitorPrice', source=source_comp, color=color, line_dash='dashed', legend_label=f'Competitor Lot {lot}', line_width=2)

p.legend.location = "top_left"
p.legend.click_policy = "hide"

hover = HoverTool(tooltips=[
    ('Lot', '@SystemCodeNumber'),
    ('Time', '@Timestamp{%F %T}'),
    ('Price', '$@Price{0.00}'),
    ('Competitor Price', '$@CompetitorPrice{0.00}')
], formatters={'@Timestamp': 'datetime'}, mode='vline')

p.add_tools(hover)

show(p)